In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly
import plotly.express as px
import warnings
warnings.filterwarnings("ignore")

plt.rcParams["figure.figsize"] = (20, 9)
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import os

In [2]:
from itertools import groupby, count

# get all the frames with blinks detected
def get_Binks(df:pd.DataFrame) -> list:
    num_blinks = []
    threshold = (max(df["EMA"]) + min(df["EAR"])) / 2
    #print("Threshold:",threshold)
    for i in range(df.shape[0]):
        if (df["EAR"].iloc[i] - df["EMA"].iloc[i]) < (threshold):
            num_blinks.append(i)
    
    return num_blinks

# NOTE: accumulate consecutive frames to get number of blinks
def accumulate_Blinks(blinks:list) -> list:
    groups = groupby(blinks, key=lambda item, c = count():item-next(c))
    final_list = [list(g) for k, g in groups]

    return final_list

# Count the number of elements in a range
def get_Count(list1, l, r):
    # Traversing the list with on line for loop
    # check if number is in range of not
    return sum( l <= x <= r for x in list1)

# NOTE: get the dictionary containing number of blinks every minute
def get_Frequency(df, result):
    freq_by_min = {}
    
    for i in df["MINUTE"].unique():
        df_tmp = df[df["MINUTE"] == i]
        freq_by_min[i] = get_Count(result, min(df_tmp["FN"]), max(df_tmp["FN"]))

    return freq_by_min


# NOTE: AMPLITUDE
def get_Amplitude(df, result):
    fn_2_amplitude = {}
    for i in result:
        fn_2_amplitude[i] = df["EAR"].iloc[i]
    
    return fn_2_amplitude

#! VELOCITY AND DURATION

# def get the frames of blink
def get_Blink_Frames(mid_frame:int, df:pd.DataFrame) -> tuple:
    start, end = mid_frame, mid_frame

    if start > 0:
        while abs(np.round(abs(df["EMA"].iloc[start]) - abs(df["EAR"].iloc[start]))) > 0:
            start -= 1
        
    if end < df.shape[0]:
        while abs(np.round(abs(df["EMA"].iloc[end]) - abs(df["EAR"].iloc[end]))) > 0:
            end += 1

    return (start+1, end + 1)

# def get the time difference
def get_Blink_Duration(mid_frame:int, df:pd.DataFrame) -> tuple:
    start, end = get_Blink_Frames(mid_frame, df)

    duration = (df["TIMESTAMP"].iloc[mid_frame] - df["TIMESTAMP"].iloc[start]) / 1000

    return duration, start, mid_frame, end

# # def get blink velocity in frames/sec
# def get_Blink_Velocity(duration:float, start:int, end:int) -> float:
#     velocity = (end - start) / duration

#     return velocity

# def get blink velocity in frames/sec
def get_Blink_Velocity(duration:float, start:int, mid:int, df:pd.DataFrame) -> float:

    EAR_S = abs(df["EAR"].iloc[start])
    EAR_M = abs(df["EAR"].iloc[mid])

    velocity = (EAR_M - EAR_S) / duration

    return velocity

# def get perclos index
def get_PERCLOS(duration_results:list, time_window:int = 60):
    TIME_INTERVAL = time_window
    PERCLOS = {}
    window = []

    for i in duration_results:
        if i[2] < TIME_INTERVAL:
            window.append((i[3] - i[1]))
        else:
            PERCLOS[TIME_INTERVAL] = window
            window = []
            TIME_INTERVAL += time_window

    return PERCLOS

# calculate perclos index
def calculate_PERCLOS(PERCLOS:dict, time_window:int = 60) -> list:
    p_index = []

    for i in PERCLOS.keys():
        p_index.append((np.sum(PERCLOS[i]) / time_window))
    
    return p_index


In [2]:
path = f"./Ashish_data/"
csvfiles = []
number_of_blinks = []
for x in os.listdir(path):
    if x.endswith(".csv"):
            csvfiles.append(x)
    #print(videofilename)
csvfiles.sort()
counter = 1
maxear = []
minear = []
duration_frames = pd.DataFrame(columns=["File_name","Start_Frame","Blink_Frame", "End_Frame"])
perclos_value=list()
for x in csvfiles:
    df_alert = pd.read_csv(f"./Ashish_data/{x}")
    if df_alert.empty:
        continue
    df_alert["EMA"] = df_alert["EAR"].ewm(8).mean()
    maxear.append(max(df_alert["EAR"]))
    minear.append(min(df_alert["EAR"]))
    
    startframe = list()
    endframe = list()
    frameno=0
    frame_no = []
    counter = 0
    for i in range(df_alert.shape[0]):
        #if (df["EAR"].iloc(i)) < (threshold):
        if (df_alert["EAR"].iloc[i-4]) - (df_alert["EAR"].iloc[i]) >= 0.12 and i>4:
            #num_blinks.append(i)
            #if counter==0:
            #    startframe = df_alert["FN"].iloc[i]
            #print("i : {} and i-4: {}".format(df_alert["FN"].iloc[i],df_alert["FN"].iloc[i-4]))
            if (df_alert["FN"].iloc[i] - 1 != frameno):
                counter += 1
                frame_no.append(df_alert["FN"].iloc[i])
                #startframe.append(df_alert["FN"].iloc[i-4])
            frameno = df_alert["FN"].iloc[i]
            #counter += 1 
        #else:
            #endframe = df_alert["FN"].iloc[i]
            #duration_frames = duration_frames.append([startframe,endframe])
            #if counter >= 8:
            #    num_of_blinks += 1
    #df_alert.dropna(inplace=True)
    number_of_blinks.append(counter)
    #print("In File : {} =====>  Frame number which is resposible for the blink detection: {}".format(x,frame_no))
    #print(startframe)
    for frame in frame_no:
        EAR_at_frameno = df_alert.loc[df_alert["FN"] == frame,"EAR"].iloc[0]
        #print(EAR_at_frameno)
        for i in range(frame,-1,-1):
            if (df_alert["EAR"].iloc[i] - EAR_at_frameno)  >= 0.1:
                startframe.append(df_alert["FN"].iloc[i-1])
                break
        for i in range(frame,df_alert.shape[0]):
            if(df_alert["EAR"].iloc[i] - EAR_at_frameno) >= 0.05:
                endframe.append(df_alert["FN"].iloc[i])
                break
    for i in range(len(endframe)):
        row_data = [x,startframe[i], frame_no[i], endframe[i]]
        oneseries = pd.Series(row_data,index= duration_frames.columns)
        duration_frames = duration_frames.append(oneseries,ignore_index=True)
    frame_no.clear()
    startframe.clear()
    endframe.clear()
    #print("Number of blinks",num_of_blinks)

    
print(number_of_blinks)
file = df_alert.to_csv("Test.csv")

[102, 4]


In [159]:
list(map(lambda x, y: '[ '+str(x)+' , '+str(y)+' ]',minear,maxear))

['[ 0.0334320673090381 , 0.4844333003592644 ]',
 '[ 0.0348007464652236 , 0.5779015817720558 ]',
 '[ 0.0338726300862058 , 0.3659948897751521 ]',
 '[ 0.020502970086939 , 0.5890605422375396 ]',
 '[ 0.0229506862661563 , 0.4784081692042131 ]',
 '[ 0.0205023737513283 , 0.8906825927937476 ]',
 '[ 0.0298073048088198 , 0.396347271312207 ]',
 '[ 0.0358186675639852 , 0.8069146489546146 ]',
 '[ 0.0329417952046427 , 0.4220152804451645 ]',
 '[ 0.0514171909541025 , 0.4719364858715518 ]',
 '[ 0.0437066879376791 , 0.4207163793716281 ]',
 '[ 0.036186964277486 , 0.6245462597923155 ]',
 '[ 0.0172500307712507 , 0.6570487714876853 ]',
 '[ 0.0229156219459715 , 0.451903956033854 ]',
 '[ 0.0412021669623398 , 0.4724127968347724 ]',
 '[ 0.0293017615905288 , 0.424755802981198 ]',
 '[ 0.0474522820774323 , 0.5018808144025202 ]',
 '[ 0.027339064826793 , 0.6565597262103922 ]',
 '[ 0.0222890306487592 , 0.4148184981483982 ]',
 '[ 0.038243208866718 , 0.610923678818523 ]',
 '[ 0.0638763171748594 , 0.6233726613292756 ]',


In [4]:
duration_frames["blinkduration"] = duration_frames["End_Frame"] - duration_frames["Start_Frame"]
duration_frames

File_name Start_Frame Blink_Frame End_Frame blinkduration
0    1_EAR.csv         474         478       492            18
1    1_EAR.csv         505         509       524            19
2    1_EAR.csv         515         517       523             8
3    1_EAR.csv         523         528       559            36
4    1_EAR.csv         566         568       588            22
..         ...         ...         ...       ...           ...
100  1_EAR.csv       14514       14516     14529            15
101  2_EAR.csv        2032        2036      2040             8
102  2_EAR.csv        4525        4528      4532             7
103  2_EAR.csv        6375        6380      8813          2438
104  2_EAR.csv        8170        8174      8179             9

[105 rows x 5 columns]

In [164]:
duration_frames[duration_frames["File_name"]=="rcam_220903_132509_EAR.csv"]

File_name Start_Frame Blink_Frame End_Frame  \
138  rcam_220903_132509_EAR.csv           9          12        15   
139  rcam_220903_132509_EAR.csv          19          21        22   
140  rcam_220903_132509_EAR.csv          27          29        30   
141  rcam_220903_132509_EAR.csv          27          31       385   
142  rcam_220903_132509_EAR.csv         179         181       186   
143  rcam_220903_132509_EAR.csv         194         197       202   
144  rcam_220903_132509_EAR.csv         226         229       240   
145  rcam_220903_132509_EAR.csv         344         346       352   
146  rcam_220903_132509_EAR.csv         360         363       368   
147  rcam_220903_132509_EAR.csv         378         380       383   
148  rcam_220903_132509_EAR.csv         382         382       383   
149  rcam_220903_132509_EAR.csv         392         395       869   
150  rcam_220903_132509_EAR.csv         437         439       443   
151  rcam_220903_132509_EAR.csv         452         455       459   
152  rcam_220903_132509_EAR.csv         870         873       874   

    blinkduration  
138             6  
139             3  
140             3  
141           358  
142             7  
143             8  
144            14  
145             8  
146             8  
147             5  
148             1  
149           477  
150             6  
151             7  
152             4

In [163]:
duration_frames.groupby(["File_name"]).agg({"Start_Frame":'count', 
                                           "Blink_Frame":'count', "End_Frame" : 'count' , "blinkduration": 'mean'})

Start_Frame  Blink_Frame  End_Frame  blinkduration
File_name                                                                     
rcam_10_EAR.csv                      20           20         20      18.350000
rcam_11_EAR.csv                      11           11         11       6.727273
rcam_220903_131827_EAR.csv            9            9          9       8.222222
rcam_220903_131908_EAR.csv           11           11         11      20.454545
rcam_220903_131948_EAR.csv            9            9          9      24.888889
rcam_220903_132028_EAR.csv            9            9          9      49.333333
rcam_220903_132108_EAR.csv           10           10         10       9.100000
rcam_220903_132148_EAR.csv           13           13         13      21.230769
rcam_220903_132229_EAR.csv           15           15         15      12.200000
rcam_220903_132309_EAR.csv            8            8          8      31.250000
rcam_220903_132349_EAR.csv            7            7          7       8.428571
rcam_220903_132429_EAR.csv           16           16         16      11.500000
rcam_220903_132509_EAR.csv           15           15         15      61.000000
rcam_220903_132549_EAR.csv            7            7          7       7.428571
rcam_220903_132630_EAR.csv           11           11         11      14.090909
rcam_220903_132710_EAR.csv            9            9          9       6.666667
rcam_220903_132750_EAR.csv           15           15         15      13.733333
rcam_220903_132830_EAR.csv           31           31         31      11.225806
rcam_220903_132910_EAR.csv           19           19         19       8.315789
rcam_220903_132950_EAR.csv           12           12         12      70.416667
rcam_220903_133030_EAR.csv           10           10         10      10.700000
rcam_220903_133111_EAR.csv           12           12         12      11.000000
rcam_220903_133152_EAR.csv           10           10         10       7.400000
rcam_220903_133232_EAR.csv            7            7          7       9.142857
rcam_220903_133313_EAR.csv           12           12         12      21.750000
rcam_220903_133354_EAR.csv           19           19         19      23.789474
rcam_220903_133434_EAR.csv           13           13         13       8.307692

In [262]:
path = f"./trip3_omsCam_2/"
csvfiles = []
number_of_blinks = []
for x in os.listdir(path):path = f"./rcam/"
csvfiles = []
number_of_blinks = []
for x in os.listdir(path):
    if x.endswith(".csv"):
            csvfiles.append(x)
    #print(videofilename)
csvfiles.sort()
counter = 1
maxear = []
minear = []
#duration_frames = pd.DataFrame(columns=["Start_Frame","End_Frame"])
perclos_value=list()
for x in csvfiles:
    df_alert = pd.read_csv(f"./rcam/{x}")
    if df_alert.empty:
        continue
    df_alert["EMA"] = df_alert["EAR"].ewm(8).mean()
    maxear.append(max(df_alert["EAR"]))
    minear.append(min(df_alert["EAR"]))
    startframe = endframe =0
    num_blinks = []
    frameno=0
    frame_no = []
    counter = num_of_blinks= 0
    for i in range(df_alert.shape[0]):
        #if (df["EAR"].iloc(i)) < (threshold):
        if(df_alert["EAR"].iloc[i]==0):
            continue
        if(abs(df_alert["EAR_L"].iloc[i] - df_alert["EAR_R"].iloc[i]) >= 0.5):
            print("EAR is higher",df_alert["FN"].iloc[i])
        if (df_alert["EAR"].iloc[i-4]) - (df_alert["EAR"].iloc[i]) >= 0.12 and i>4:
            #num_blinks.append(i)
            #if counter==0:
            #    startframe = df_alert["FN"].iloc[i]
            #print("i : {} and i-4: {}".format(df_alert["FN"].iloc[i],df_alert["FN"].iloc[i-4]))
            if (df_alert["FN"].iloc[i] - 1 != frameno and df_alert["EAR_diff_LAR"].iloc[i]<0.4):
                counter += 1
                if df_alert["EAR"].iloc[i] < df_alert["EAR"].iloc[i-1]:
                    frame_no.append(df_alert["FN"].iloc[i])
                else:
                    frame_no.append(df_alert["FN"].iloc[i-1])
                #startframe.append(df_alert["FN"].iloc[i-4])
            frameno = df_alert["FN"].iloc[i]
            
            #counter += 1 
        #else:
            #endframe = df_alert["FN"].iloc[i]
            #duration_frames = duration_frames.append([startframe,endframe])
            #if counter >= 8:
            #    num_of_blinks += 1
    #df_alert.dropna(inplace=True)
    number_of_blinks.append(counter)
    print("In File : {} =====>  Frame number which is resposible for the blink detection: {}".format(x,frame_no))
    counter = 0
    frame_no.clear()
    
    #print("Number of blinks",num_of_blinks)

    
print(number_of_blinks)
file = df_alert.to_csv("Test.csv")

KeyError: 'EAR_L'

In [278]:
from tokenize import Name


path = f"./rcam/"
csvfiles = []
number_of_blinks = []
for x in os.listdir(path):
    if x.endswith(".csv"):
            csvfiles.append(x)
    #print(videofilename)
csvfiles.sort()
counter = 1
duration_frames = []
perclos_value=list()
for x in csvfiles:
    df_alert = pd.read_csv(f"./rcam/{x}")
    if df_alert.empty:
        continue
    mean, std_dev = df_alert["EAR"].describe()[1], df_alert["EAR"].describe()[2]
    df_alert["EMA"] = df_alert["EAR"].ewm(alpha=0.12).mean()
    startframe = endframe =0
    num_blinks = []
    counter = num_of_blinks= 0
    for i in range(df_alert.shape[0]):
        #if (df["EAR"].iloc(i)) < (threshold):
        if (df_alert["EAR"].iloc[i]) < (df_alert["EMA"].iloc[i]):
            num_blinks.append(i)
            counter += 1 
        else:
            if counter > 8:
                #duration_frames.append(df_alert["FN"].iloc[i]-8)
                #duration_frames.append(df_alert["FN"].iloc[i])
                num_of_blinks += 1
    #df_alert.dropna(inplace=True)
            counter = 0
    number_of_blinks.append(num_of_blinks)
    #print("Number of blinks",num_of_blinks)

    #plt.figure()
    #sns.lineplot(data= df_alert[["FN","EAR"]], x="FN",y="EAR")
    print("Frame number when EAR is less than threshold for the video: ", x)
    #print(duration_frames)
    #nparray_duration_frame = np.array(duration_frames)
    #result = nparray_duration_frame/20
    #print(result.tolist())
    #duration_frames.clear()
    fig = make_subplots(rows=1, cols=1)


    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = df_alert["EAR"],  name = "EAR", mode = "lines"),
        row=1, col=1
    )
    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = df_alert["EMA"],  name = "EMA", mode = "lines"),
        row=1, col=1
    )
    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = [np.mean(df_alert["EMA"])] * df_alert.shape[0],  name = "EMA_MEAN", mode = "lines"),
        row=1, col=1
    )
    fig.update_layout(height=450, width=1550, title_text="EAR with EMA: "+ x + "       Number of blinks: "+ str(num_of_blinks))
    fig.show()

print(number_of_blinks)

Frame number when EAR is less than threshold for the video:  rcam_11_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_1_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_220903_131827_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_220903_131908_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_220903_131948_EAR.csv


...

Frame number when EAR is less than threshold for the video:  rcam_220903_133232_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_220903_133313_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_220903_133354_EAR.csv


Frame number when EAR is less than threshold for the video:  rcam_220903_133434_EAR.csv


[10, 14, 5, 12, 13, 12, 14, 12, 13, 11, 8, 12, 19, 16, 14, 14, 14, 17, 14, 8, 8, 15, 11, 12, 10, 12, 7]


In [265]:
df_alert = pd.read_csv(f"myvideo2_EAR.csv")
counter = 1
maxear = []
minear = []
duration_frames = pd.DataFrame(columns=["File_name","Start_Frame","Blink_Frame", "End_Frame"])
perclos_value=list()
df_alert["EMA"] = df_alert["EAR"].ewm(8).mean()
maxear.append(max(df_alert["EAR"]))
minear.append(min(df_alert["EAR"]))
number_of_blinks = []    
startframe = list()
endframe = list()
frameno=0
frame_no = []
counter = 0
df_alert["EAR_diff_LAR"] = abs(df_alert["EAR_L"]-df_alert["EAR_R"])
for i in range(df_alert.shape[0]):
        #if (df["EAR"].iloc(i)) < (threshold):
    if(df_alert["EAR"].iloc[i]==0):
        continue
    if (df_alert["EAR"].iloc[i-4]) - (df_alert["EAR"].iloc[i]) >= 0.12 and i>4:
            #num_blinks.append(i)
            #if counter==0:
            #    startframe = df_alert["FN"].iloc[i]
            #print("i : {} and i-4: {}".format(df_alert["FN"].iloc[i],df_alert["FN"].iloc[i-4]))
        if (df_alert["FN"].iloc[i] - 1 != frameno and df_alert["EAR_diff_LAR"].iloc[i]<0.4):
            counter += 1
            if df_alert["EAR"].iloc[i] < df_alert["EAR"].iloc[i-1]:
                frame_no.append(df_alert["FN"].iloc[i])
            else:
                frame_no.append(df_alert["FN"].iloc[i-1])
                #startframe.append(df_alert["FN"].iloc[i-4])
        frameno = df_alert["FN"].iloc[i]
            #counter += 1 
        #else:
            #endframe = df_alert["FN"].iloc[i]
            #duration_frames = duration_frames.append([startframe,endframe])
            #if counter >= 8:
            #    num_of_blinks += 1
    #df_alert.dropna(inplace=True)
number_of_blinks.append(counter)
    #print("In File : {} =====>  Frame number which is resposible for the blink detection: {}".format(x,frame_no))
    #print(startframe)
for frame in frame_no:
    EAR_at_frameno = df_alert.loc[df_alert["FN"] == frame,"EAR"].iloc[0]

    for i in range(frame,-1,-1):
        if (df_alert["EAR"].iloc[i] - EAR_at_frameno)  >= 0.1:
            startframe.append(df_alert["FN"].iloc[i-1])
            break
    for i in range(frame,df_alert.shape[0]):
        if(df_alert["EAR"].iloc[i] - EAR_at_frameno) >= 0.05:
            endframe.append(df_alert["FN"].iloc[i])
            break
for i in range(len(endframe)):
    row_data = [x,startframe[i], frame_no[i], endframe[i]]
    oneseries = pd.Series(row_data,index= duration_frames.columns)
    duration_frames = duration_frames.append(oneseries,ignore_index=True)
print(frame_no)
frame_no.clear()
startframe.clear()
endframe.clear()
    #print("Number of blinks",num_of_blinks)
print(number_of_blinks)



[7, 125, 148, 264, 275, 290]
[6]


In [264]:
duration_frames["duration_of_blink"]= duration_frames["End_Frame"]-duration_frames["Start_Frame"]
duration_frames

File_name Start_Frame Blink_Frame End_Frame duration_of_blink
0  rcam_10_EAR.csv           7           7         8                 1
1  rcam_10_EAR.csv         123         125       184                61
2  rcam_10_EAR.csv         146         148       265               119
3  rcam_10_EAR.csv         264         264       278                14
4  rcam_10_EAR.csv         273         275       341                68

In [221]:
value = np.linalg.norm(140-134)
print(value)

6.0


In [254]:
df_alert.describe()

FN       EAR_L       EAR_R         EAR         EMA
count  348.000000  348.000000  348.000000  348.000000  348.000000
mean   174.500000    0.406236    0.350651    0.378444    0.382049
std    100.603181    0.383767    0.270533    0.264205    0.231742
min      1.000000    0.000000    0.000000    0.000000    0.051800
25%     87.750000    0.208117    0.184675    0.200772    0.209126
50%    174.500000    0.365823    0.343493    0.369443    0.368525
75%    261.250000    0.417837    0.418316    0.446249    0.485105
max    348.000000    2.296015    1.399153    1.381502    1.011797

In [255]:
df_alert["EAR_diff_LAR"] = abs(df_alert["EAR_L"]-df_alert["EAR_R"])

In [258]:
df_alert[df_alert["EAR_diff_LAR"]>0.4].head(60)

FN     EAR_L     EAR_R       EAR                       p1  \
31    32  1.032523  0.459554  0.746039  [0.71887892 0.42003733]   
32    33  1.098619  0.458143  0.778381  [0.71803844 0.42086416]   
33    34  1.298167  0.452649  0.875408  [0.71911556 0.42200452]   
34    35  1.352746  0.419947  0.886347  [0.71971947 0.42234275]   
35    36  1.367743  0.447314  0.907528  [0.71920383 0.42484996]   
36    37  1.942733  0.299949  1.121341  [0.7201736  0.43786448]   
37    38  1.619684  0.308477  0.964080  [0.72062701 0.43549243]   
38    39  1.461802  0.372370  0.917086  [0.72075367 0.4298256 ]   
39    40  1.525265  0.435461  0.980363  [0.72280657 0.42990685]   
40    41  1.573633  0.425024  0.999328  [0.72384423 0.42745867]   
41    42  1.462253  0.441693  0.951973  [0.72817832 0.42995173]   
42    43  1.654277  0.444075  1.049176  [0.73006833 0.42924833]   
43    44  1.888281  0.439957  1.164119  [0.733742   0.43299922]   
44    45  1.785184  0.467498  1.126341  [0.73459089 0.42945397]   
45    46  2.296015  0.466989  1.381502  [0.73664784 0.43229768]   
46    47  1.750326  0.453165  1.101746  [0.7354697  0.43536761]   
47    48  1.583050  0.457579  1.020314  [0.73494506 0.43480092]   
48    49  1.633124  0.471486  1.052305  [0.73499    0.44279265]   
49    50  1.412634  0.453015  0.932825  [0.73610747 0.44160205]   
50    51  1.332312  0.447012  0.889662  [0.73409039 0.43988699]   
51    52  1.570416  0.466402  1.018409  [0.7350114  0.43761194]   
52    53  1.914901  0.436454  1.175678  [0.73314679 0.43142623]   
53    54  1.613415  0.450710  1.032063  [0.73331666 0.43588173]   
54    55  1.506424  0.427439  0.966931  [0.73119038 0.43817019]   
55    56  1.658329  0.426805  1.042567  [0.73079091 0.43625841]   
56    57  1.680781  0.434611  1.057696  [0.72548443 0.44054341]   
57    58  1.456184  0.376607  0.916395  [0.72128946 0.43417549]   
58    59  0.766313  0.328577  0.547445  [0.71534979 0.43200997]   
59    60  1.323634  0.240670  0.782152  [0.704768   0.43456978]   
60    61  0.655786  0.192099  0.423943  [0.69321972 0.43177533]   
95    96  0.431668  1.165852  0.798760  [0.35280466 0.38957363]   
96    97  0.416411  1.172862  0.794636  [0.33621949 0.39528394]   
97    98  0.423147  1.212362  0.817755  [0.32195798 0.40009028]   
98    99  0.304207  1.297091  0.800649  [0.31350034 0.39632201]   
99   100  0.336603  0.995136  0.665869  [0.30179435 0.40587583]   
100  101  0.445750  0.969556  0.707653  [0.29506239 0.41680658]   
101  102  0.336137  0.811497  0.573817  [0.29191285 0.42047244]   
102  103  0.302018  0.770214  0.536116  [0.28562626 0.42825133]   
104  105  0.353572  1.274628  0.814100  [0.27562726 0.43200737]   
105  106  0.372378  0.977440  0.674909  [0.27040344 0.4352994 ]   
106  107  0.353925  1.077728  0.715826  [0.27005354 0.43752205]   
107  108  0.387894  0.998361  0.693127  [0.26941538 0.44039506]   
108  109  0.381779  0.998975  0.690377  [0.2673744  0.44004422]   
109  110  0.320269  0.841889  0.581079  [0.26866335 0.44019535]   
110  111  0.272469  0.902108  0.587289  [0.26845443 0.43521005]   
111  112  0.254556  1.084231  0.669394  [0.27131623 0.43643999]   
112  113  0.330622  0.992517  0.661570  [0.26582718 0.43894655]   
113  114  0.273318  1.222463  0.747891  [0.26535326 0.44145769]   
114  115  0.282251  1.119287  0.700769  [0.26363581 0.43954682]   
115  116  0.343514  1.271183  0.807349  [0.26299772 0.44454774]   
116  117  0.274973  1.176182  0.725578  [0.26658499 0.44064012]   
117  118  0.333054  0.967966  0.650510  [0.26641712 0.44307166]   
118  119  0.368554  0.999675  0.684115  [0.26775062 0.44059327]   
119  120  0.342053  0.879144  0.610599  [0.27240244 0.44064668]   
120  121  0.419207  1.202492  0.810850  [0.2795338  0.43886894]   
121  122  0.394696  1.339357  0.867027  [0.29007876 0.43189299]   
122  123  0.304206  1.399153  0.851680  [0.3044298  0.42460299]   
123  124  0.305380  1.315919  0.810650  [0.32428673 0.41984862]   

                          p2                       p